# Capstone Project week 5 Battle of the Neighbourhoods

# Selecting the Best Location for an Italian Restaurant in Amsterdam

## Introduction

In this report we will explore what would be the best location to open an Italian restaurant in the Amsterdam the most capital of The Netherlands.

Amsterdam is the capital and most populous city of the Netherlands with a population of 872,680 within the city proper, 1,558,755 in the urban area. It is an attractive town that is popular with tourists but also for families and expats due to its large International School and location near to Schiphol Airport. The city has many restaurants of all nationalities and is famous for its nightlife.

The business plan for the Italian restaurant aims to open a high quality Italian restaurant in Amsterdam with at least 70 seats. The real estate agent has provided several locations that meet the requirements of the building: at least 130 square meters for customers, at least 35 square meters for the kitchen, right permits on the building to start a restaurant.

As the selected locations for the Italian restaurant are more or less comparable, the final decision for the location of the Italian restaurant will therefore be based on the neighbourhood. The Italian restaurant wants to know the following things about the neighbourhoods of each restaurant:

1. How comparable are the neighbourhoods?
2. How many competing Italian restaurant are available in these neighbourhoods?

## Data

Based on problem definition, factors that will influence our decision are:

1. Definition of neighbourhoods in Amsterdam. Source: data from the city of Amsterdam: 'https://allecijfers.nl/gemeente-overzicht/amsterdam/'. Data will be collected by web scraping.
2. Venues within each neighbourhood. Source: Foursquare. Data will be collected by using an API. 
3. Existing Italian restaurants in the neighborhood (only Italian restaurants). Source: Foursquare. Data will be collected by using an API.
4. List of suitable locations for a new Italian Restaurant. Source: provided by real estate agent. Excel file. 


## Methods

First we examine the comparability of each neighbourhood. Thereafter we describe how we examined the competing Italian restaurants. 

Comparing neighbourhoods
First data is needed to define the neighbourhoods. For this we use data from the city of Amsterdam: 'https://allecijfers.nl/gemeente-overzicht/amsterdam/'. Webscraping within Python is used to collect actual data from this website. After collecting the data, we cleaned it (removed disturbing lines that did not contain  information about neighbourhoods), added information on the latitude and longitude of each location by using Geolocator and we plotted each neighbourhood on a map of Amsterdam. 
Next data on the venues in Amsterdam was needed. We used data from Foursquare for this purpose and built an API to collect real time location data on all venues in a neighbourhood. 
Combing the data on the neighbourhoods and the venues is the next step. Then the information was grouped to the top 5 venues in each neighbourhood. However Amsterdam has over 400 neighbourhoods so a smarter way to measure comparability of neighbourhoods is needed.
Artificial Intelligence is used to measure the comparability of the neighbourhoods. For this particular problem K means clustering was selected because it is an unsupervised AI method, which is very suitable for our goals since we do not know the differences between all neighbourhoods. We distinguish 20 neighbourhoods out of the more than 400 neighbourhoods in Amsterdam. The final result of the neighbourhoods will be plotted on a map of Amsterdam. Also an overview of the characteristics of each cluster will be provided.

Analyzing competing Italian restaurants in Amsterdam
Starting point is data on the Italian restaurants in Amsterdam. This will be collected with an API on Foursquare. This data will be grouped with the earlier collected information on the Amsterdam neighbourhoods. The result of this step is an analysis of Italian restaurants in each neighbourhood of Amsterdam. Also a map of all Italian restaurants in Amsterdam is provided. 
The postal codes as provided by the real estate agent will be used to select only the competing Italian restaurants near each selected location. This leads to the final result: a table of all competing italian restaurants near each selected location.


### 1. Comparing neighbourhoods in Amsterdam

#### Import the needed libraries

In [1]:
import pandas as pd
import numpy as np



#### Import the data from the Amsterdam neighborhoods¶

In [2]:
url = 'https://allecijfers.nl/gemeente-overzicht/amsterdam/'

In [3]:
# import the data from the website 
df = pd.read_html(url, header=0)
type(df)

list

In [4]:
df1 =df[0]
df1

Naam     Regio   Postcode  Aantal inwoners
0                    Amsterdam  Gemeente  1011-1109          872.757
1        Burgwallen Oude Zijde      Wijk       1012            4.465
2                  Kop Zeedijk     Buurt       1012            1.100
3        Oude Kerk en omgeving     Buurt       1012          730.000
4              Burgwallen Oost     Buurt       1012            1.610
..                         ...       ...        ...              ...
497             Gein Noordoost     Buurt       1106            3.265
498              Gein Zuidoost     Buurt       1107            3.370
499                   Driemond      Wijk       1109            1.620
500              Dorp Driemond     Buurt       1109            1.490
501  Landelijk gebied Driemond     Buurt       1109          130.000

[502 rows x 4 columns]

In [5]:
# clean the data; drop rows when Regio is not equal to Buurt. A regio contains multiple neighbourhoods 
Adambuurt = df1[ df1['Regio'] != 'Buurt'].index
# Delete these row indexes from dataFrame
df1.drop(Adambuurt , inplace=True)
df1 = df1.reset_index(drop=True)
df1.head(20)


Naam  Regio   Postcode  Aantal inwoners
0               Kop Zeedijk  Buurt       1012            1.100
1     Oude Kerk en omgeving  Buurt       1012          730.000
2           Burgwallen Oost  Buurt       1012            1.610
3           Nes en omgeving  Buurt       1012          350.000
4    Bg terrein en omgeving  Buurt       1012          670.000
5                 Hemelrijk  Buurt       1012          575.000
6         Nieuwendijk Noord  Buurt       1012          460.000
7          Spuistraat Noord  Buurt       1012          825.000
8   Nieuwe Kerk en omgeving  Buurt       1012          820.000
9           Spuistraat Zuid  Buurt  1012-1016          720.000
10           Begijnhofbuurt  Buurt       1012          415.000
11           Kalverdriehoek  Buurt       1012          305.000
12  Langestraat en omgeving  Buurt       1015            1.870
13  Leliegracht en omgeving  Buurt  1015-1016            1.820
14       Felix Meritisbuurt  Buurt       1016            2.055
15       Leidsegracht Noord  Buurt       1016          685.000
16             Spiegelbuurt  Buurt       1017          820.000
17             Gouden Bocht  Buurt       1017          145.000
18            Van Loonbuurt  Buurt       1017            1.415
19          Amstelveldbuurt  Buurt       1017            1.510

In [6]:
print(df1.shape)

(403, 4)


#### Combine the neighbourhood data with latitude and longitudes

In this step we combine the previously defined table with the information of the neighbourhoods with information of the latitude and longitude of each neighbourhood. This enables us to plot the neighbourhoods on a map. 

In [7]:
#Import the needed libraries
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip -q install folium
#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [8]:
# import Amsterdam location 

address = 'Amsterdam, The Netherlands'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Amsterdam are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Amsterdam are 52.3727598, 4.8936041.


In [9]:
# Get the latitude and longitude based on the postal codes.
! pip install geocoder

import geocoder

def get_latilong(postal_code):
    lati_long_coords = None
    while(lati_long_coords is None):
        g = geocoder.arcgis('{}, Amsterdam, The Netherlands'.format(postal_code))
        lati_long_coords = g.latlng
    return lati_long_coords
    
get_latilong('1012')

     |████████████████████████████████| 98 kB 6.1 MB/s  eta 0:00:01


[52.37365079600005, 4.895563798000069]

In [10]:
# Retrieving Postal Code Coordinates for each neighborhood
postal_codes = df1['Postcode']    
coords = [ get_latilong(postal_code) for postal_code in postal_codes.tolist() ]

In [11]:
# Adding Columns Latitude & Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])
df1['Latitude'] = df_coords['Latitude']
df1['Longitude'] = df_coords['Longitude']

In [12]:
df1.head()
# This results in a table with the Name of the neighbourhood, the classification that is it a neighbourhood, postal code, inhabitants, latitude and longitude

Naam  Regio Postcode  Aantal inwoners   Latitude  \
0             Kop Zeedijk  Buurt     1012             1.10  52.373651   
1   Oude Kerk en omgeving  Buurt     1012           730.00  52.373651   
2         Burgwallen Oost  Buurt     1012             1.61  52.373651   
3         Nes en omgeving  Buurt     1012           350.00  52.373651   
4  Bg terrein en omgeving  Buurt     1012           670.00  52.373651   

   Longitude  
0   4.895564  
1   4.895564  
2   4.895564  
3   4.895564  
4   4.895564

The data preparation phase for the neighborhoods is now completed.

#### Make a map of Amsterdam and its neighbourhoods

In [13]:
# create map of Amsterdam using latitude and longitude values
map_amsterdam = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, lng, naam, in zip(df1['Latitude'], df1['Longitude'], df1['Naam']):
    #label = '{}. {} 'format(naam)
    label = '{}'.format(naam)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_amsterdam)
map_amsterdam

Now we are ready to combine the data of the neighbourhoods with the information on the venues in the neighbourhoods. This information will be gathered from Foursquare.

#### Collecting information form Foursquare

##### Setting up the API: define Foursquare Credentials and Version

In [14]:
CLIENT_ID = 'SXDNLURY1D511PCTGJG2HD31ZIBB0UU1FOQ1EACUQR5Y22JV' # your Foursquare ID
CLIENT_SECRET = '3Q4DBIWXY4F5KCJCZVZ1CJ4CN1VMD4ODEQ203OIA0QANILBV' # your Foursquare Secret
VERSION = '20180604' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: SXDNLURY1D511PCTGJG2HD31ZIBB0UU1FOQ1EACUQR5Y22JV
CLIENT_SECRET:3Q4DBIWXY4F5KCJCZVZ1CJ4CN1VMD4ODEQ203OIA0QANILBV


##### Collect the information on the venues from Foursqare

In [15]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [16]:
df = df1
amsterdam_venues = getNearbyVenues(names=df['Naam'], latitudes=df['Latitude'],longitudes=df['Longitude'])

Kop Zeedijk
Oude Kerk en omgeving
Burgwallen Oost
Nes en omgeving
Bg terrein en omgeving
Hemelrijk
Nieuwendijk Noord
Spuistraat Noord
Nieuwe Kerk en omgeving
Spuistraat Zuid
Begijnhofbuurt
Kalverdriehoek
Langestraat en omgeving
Leliegracht en omgeving
Felix Meritisbuurt
Leidsegracht Noord
Spiegelbuurt
Gouden Bocht
Van Loonbuurt
Amstelveldbuurt
Rembrandtpleinbuurt
Reguliersbuurt
Leidsegracht Zuid
Oosterdokseiland
Scheepvaarthuisbuurt
Rapenburg
Lastage
Nieuwmarkt
Uilenburg
Valkenburg
Zuiderkerkbuurt
Waterloopleinbuurt
Westerdokseiland
Haarlemmerbuurt Oost
Haarlemmerbuurt West
Westelijke Eilanden
Planciusbuurt Noord
Planciusbuurt Zuid
Driehoekbuurt
Bloemgrachtbuurt
Marnixbuurt Noord
Zaagpoortbuurt
Marnixbuurt Midden
Elandsgrachtbuurt
Passeerdersgrachtbuurt
Groenmarktkadebuurt
Marnixbuurt Zuid
Anjeliersbuurt Noord
Anjeliersbuurt Zuid
Leidsebuurt Noordwest
Leidsebuurt Zuidwest
Leidsebuurt Noordoost
Leidsebuurt Zuidoost
Weteringbuurt
Den Texbuurt
Utrechtsebuurt Zuid
Frederikspleinbuurt
Weesp

In [17]:
print(amsterdam_venues.shape)
amsterdam_venues.head()

(15293, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Kop Zeedijk              52.373651                4.895564   
1  Kop Zeedijk              52.373651                4.895564   
2  Kop Zeedijk              52.373651                4.895564   
3  Kop Zeedijk              52.373651                4.895564   
4  Kop Zeedijk              52.373651                4.895564   

                           Venue  Venue Latitude  Venue Longitude  \
0            De Koffieschenkerij       52.374043         4.898427   
1                            Dam       52.373005         4.892929   
2                 Wynand Fockink       52.372301         4.895253   
3     Old Amsterdam Cheese Store       52.374862         4.895301   
4  Proeflokaal De Drie Fleschjes       52.374203         4.892239   

  Venue Category  
0    Coffee Shop  
1          Plaza  
2   Liquor Store  
3    Cheese Shop  
4            Bar

In [18]:
amsterdam_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                    
Aalsmeerwegbuurt Oost                                      15   
Aalsmeerwegbuurt West                                      15   
Alexanderplein en omgeving                                 54   
Amstel Iii Deel A B Zuid                                    1   
Amstelkwartier Noord                                       28   
Amstelkwartier West                                        28   
Amstelveldbuurt                                            81   
Amsterdamse Poort                                          44   
Andreasterrein                                             34   
Anjeliersbuurt Noord                                      100   
Anjeliersbuurt Zuid                                       100   
Architectenbuurt                                           46   
Baanakkerspark Noord                                        9   
Baanakkerspark Zuid                                         9   
Balboaplein en omgeving                                    57   
Banne Noordoost                                            11   
Banne Noordwest                                            11   
Banne Zuidoost                                             11   
Banne Zuidwest                                             11   
Banpleinbuurt                                             100   
Bedrijventerrein Hamerstraat                               14   
Bedrijventerrein Landlust                                  49   
Beethovenbuurt                                             23   
Begijnhofbuurt                                             70   
Belgiëplein en omgeving                                     4   
Bellamybuurt Noord                                        100   
Bellamybuurt Zuid                                         100   
Bertelmanpleinbuurt                                        35   
Betondorp                                                   4   
Bg terrein en omgeving                                     70   
Bijlmermuseum Noord                                         8   
Bijlmermuseum Zuid                                          8   
Blauwe Zand                                                28   
Bloemenbuurt Noord                                         22   
Bloemenbuurt Zuid                                          22   
Bloemgrachtbuurt                                          100   
Borgerbuurt                                               100   
Borneo                                                     46   
Bosleeuw                                                   49   
Buiksloterbreek                                            11   
Buiksloterdijk Oost                                        28   
Buiksloterdijk West                                        11   
Buikslotermeer Noord                                       28   
Buikslotermeerplein                                        28   
Buitenveldert Midden Zuid                                  35   
Buitenveldert Oost Midden                                  35   
Buitenveldert West Midden                                   6   
Buitenveldert Zuidoost                                     35   
Buitenveldert Zuidwest                                      6   
Burgemeester Tellegenbuurt Oost                           100   
Burgemeester Tellegenbuurt West                           100   
Burgwallen Oost                                            70   
Buurt 10                                                    1   
Buurt 2                                                    22   
Buurt 3                                                    22   
Buurt 4 Oost                                               22   
Buurt 5 Noord                                               8   
Buurt 5 Zuid                                                8   
Buurt 6                                                     1   
Buurt 7                                                     1   
Buurt 8   

In [19]:
print('There are {} uniques categories.'.format(len(amsterdam_venues['Venue Category'].unique())))

There are 280 uniques categories.


#### Analyze Each Neighborhood

In [20]:
amsterdam_onehot = pd.get_dummies(amsterdam_venues[['Venue Category']], prefix="", prefix_sep="")

amsterdam_onehot['Naam'] = amsterdam_venues['Neighborhood'] 

fixed_columns = [amsterdam_onehot.columns[-1]] + list(amsterdam_onehot.columns[:-1])
amsterdam_onehot = amsterdam_onehot[fixed_columns]

amsterdam_onehot.head()

Naam  Accessories Store  Afghan Restaurant  African Restaurant  \
0  Kop Zeedijk                  0                  0                   0   
1  Kop Zeedijk                  0                  0                   0   
2  Kop Zeedijk                  0                  0                   0   
3  Kop Zeedijk                  0                  0                   0   
4  Kop Zeedijk                  0                  0                   0   

   American Restaurant  Aquarium  Arcade  Argentinian Restaurant  Art Gallery  \
0                    0         0       0                       0            0   
1                    0         0       0                       0            0   
2                    0         0       0                       0            0   
3                    0         0       0                       0            0   
4                    0         0       0                       0            0   

   Art Museum  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0           0                    0                     0                 0   
1           0                    0                     0                 0   
2           0                    0                     0                 0   
3           0                    0                     0                 0   
4           0                    0                     0                 0   

   Athletics & Sports  Australian Restaurant  Auto Garage  Auto Workshop  \
0                   0                      0            0              0   
1                   0                      0            0              0   
2                   0                      0            0              0   
3                   0                      0            0              0   
4                   0                      0            0              0   

   BBQ Joint  Bagel Shop  Bakery  Bar  Baseball Stadium  Beach  Beach Bar  \
0          0           0       0    0                 0      0          0   
1          0           0       0    0                 0      0          0   
2          0           0       0    0                 0      0          0   
3          0           0       0    0                 0      0          0   
4          0           0       0    1                 0      0          0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0                0         0            0           0                   0   
1                0         0            0           0                   0   
2                0         0            0           0                   0   
3                0         0            0           0                   0   
4                0         0            0           0                   0   

   Bike Rental / Bike Share  Bike Shop  Bistro  Boarding House  Boat or Ferry  \
0                         0          0       0               0              0   
1                         0          0       0               0              0   
2                         0          0       0               0              0   
3                         0          0       0               0              0   
4                         0          0       0               0              0   

   Bookstore  Boutique  Brasserie  Breakfast Spot  Brewery  Bridal Shop  \
0          0         0          0               0        0            0   
1          0         0          0               0        0            0   
2          0         0          0               0        0            0   
3          0         0          0               0        0            0   
4          0         0          0               0        0            0   

   Bridge  Burger Joint  Burrito Place  Bus Line  Bus Station  Bus Stop  \
0       0             0              0         0            0         0   
1       0             0              0         0            0         0   
2       0             0              0         0   

In [21]:
amsterdam_onehot.shape

(15293, 281)

In [22]:
amsterdam_grouped = amsterdam_onehot.groupby('Naam').mean().reset_index()
amsterdam_grouped

Naam  Accessories Store  \
0                     Aalsmeerwegbuurt Oost               0.00   
1                     Aalsmeerwegbuurt West               0.00   
2                Alexanderplein en omgeving               0.00   
3                  Amstel Iii Deel A B Zuid               0.00   
4                      Amstelkwartier Noord               0.00   
5                       Amstelkwartier West               0.00   
6                           Amstelveldbuurt               0.00   
7                         Amsterdamse Poort               0.00   
8                            Andreasterrein               0.00   
9                      Anjeliersbuurt Noord               0.00   
10                      Anjeliersbuurt Zuid               0.00   
11                         Architectenbuurt               0.00   
12                     Baanakkerspark Noord               0.00   
13                      Baanakkerspark Zuid               0.00   
14                  Balboaplein en omgeving               0.00   
15                          Banne Noordoost               0.00   
16                          Banne Noordwest               0.00   
17                           Banne Zuidoost               0.00   
18                           Banne Zuidwest               0.00   
19                            Banpleinbuurt               0.00   
20             Bedrijventerrein Hamerstraat               0.00   
21                Bedrijventerrein Landlust               0.00   
22                           Beethovenbuurt               0.00   
23                           Begijnhofbuurt               0.00   
24                  Belgiëplein en omgeving               0.00   
25                       Bellamybuurt Noord               0.00   
26                        Bellamybuurt Zuid               0.00   
27                      Bertelmanpleinbuurt               0.00   
28                                Betondorp               0.00   
29                   Bg terrein en omgeving               0.00   
30                      Bijlmermuseum Noord               0.00   
31                       Bijlmermuseum Zuid               0.00   
32                              Blauwe Zand               0.00   
33                       Bloemenbuurt Noord               0.00   
34                        Bloemenbuurt Zuid               0.00   
35                         Bloemgrachtbuurt               0.00   
36                              Borgerbuurt               0.00   
37                                   Borneo               0.00   
38                                 Bosleeuw               0.00   
39                          Buiksloterbreek               0.00   
40                      Buiksloterdijk Oost               0.00   
41                      Buiksloterdijk West               0.00   
42                     Buikslotermeer Noord               0.00   
43                      Buikslotermeerplein               0.00   
44                Buitenveldert Midden Zuid               0.00   
45                Buitenveldert Oost Midden               0.00   
46                Buitenveldert West Midden               0.00   
47                   Buitenveldert Zuidoost               0.00   
48                   Buitenveldert Zuidwest               0.00   
49          Burgemeester Tellegenbuurt Oost               0.01   
50          Burgemeester Tellegenbuurt West               0.01   
51                          Burgwallen Oost               0.00   
52                                 Buurt 10               0.00   
53                                  Buurt 2               0.00   
54                                  Buurt 3               0.00   
55                             Buurt 4 Oost               0.00   
56                            Buurt 5 Noord               0.00   
57                             Buurt 5 Zuid               0.00   
58                                  Buurt 6               0.00   
59                                  Buurt 7               0.00   
60           

In [23]:
amsterdam_grouped.shape

(403, 281)

### Analyze the top 5 venues in each neighbourhood¶

In [24]:
num_top_venues = 5
for neigh in amsterdam_grouped['Naam']:
    print("----"+neigh+"----")
    temp = amsterdam_grouped[amsterdam_grouped['Naam'] == neigh].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Aalsmeerwegbuurt Oost----
                 venue  freq
0           Restaurant  0.13
1               Office  0.13
2                Diner  0.07
3  Sporting Goods Shop  0.07
4         Soccer Field  0.07


----Aalsmeerwegbuurt West----
                 venue  freq
0           Restaurant  0.13
1               Office  0.13
2                Diner  0.07
3  Sporting Goods Shop  0.07
4         Soccer Field  0.07


----Alexanderplein en omgeving----
         venue  freq
0  Zoo Exhibit  0.26
1   Restaurant  0.04
2         Café  0.04
3  Coffee Shop  0.04
4          Bar  0.04


----Amstel Iii Deel A B Zuid----
               venue  freq
0        Golf Course   1.0
1  Accessories Store   0.0
2          Newsstand   0.0
3    Organic Grocery   0.0
4       Optical Shop   0.0


----Amstelkwartier Noord----
                  venue  freq
0                 Hotel  0.14
1          Dance Studio  0.11
2            Restaurant  0.11
3           Auto Garage  0.04
4  Gym / Fitness Center  0.04


----Amstelkwartie

         venue  freq
0  Zoo Exhibit  0.26
1   Restaurant  0.04
2         Café  0.04
3  Coffee Shop  0.04
4          Bar  0.04


----D Buurt----
                venue  freq
0  Chinese Restaurant  0.07
1              Bakery  0.07
2         Supermarket  0.07
3      Clothing Store  0.05
4  Italian Restaurant  0.05


----Da Costabuurt Noord----
                venue  freq
0                Café  0.05
1                 Bar  0.05
2  Italian Restaurant  0.04
3          Restaurant  0.04
4         Coffee Shop  0.04


----Da Costabuurt Zuid----
                venue  freq
0                Café  0.05
1                 Bar  0.05
2  Italian Restaurant  0.04
3          Restaurant  0.04
4         Coffee Shop  0.04


----Dapperbuurt Noord----
                 venue  freq
0          Coffee Shop  0.08
1   Italian Restaurant  0.06
2                 Café  0.06
3                  Bar  0.06
4  Sporting Goods Shop  0.04


----Dapperbuurt Zuid----
         venue  freq
0         Café  0.08
1       Market  0.08
2

             venue  freq
0     Soccer Field   0.5
1     Hockey Field   0.5
2     Neighborhood   0.0
3  Organic Grocery   0.0
4     Optical Shop   0.0


----Haveneiland Zuidwest Rieteiland West----
             venue  freq
0     Soccer Field   0.5
1     Hockey Field   0.5
2     Neighborhood   0.0
3  Organic Grocery   0.0
4     Optical Shop   0.0


----Helmersbuurt Oost----
                           venue  freq
0                           Café  0.06
1           Ethiopian Restaurant  0.05
2                            Bar  0.05
3                    Coffee Shop  0.04
4  Vegetarian / Vegan Restaurant  0.04


----Hemelrijk----
           venue  freq
0          Hotel  0.11
1    Coffee Shop  0.06
2            Bar  0.06
3  Deli / Bodega  0.04
4           Café  0.04


----Hemonybuurt----
                venue  freq
0  Italian Restaurant  0.08
1                Café  0.06
2         Coffee Shop  0.05
3         Supermarket  0.03
4         Yoga Studio  0.03


----Hercules Seghersbuurt----
           

            venue  freq
0      Restaurant  0.08
1     Coffee Shop  0.08
2          Bakery  0.05
3           Hotel  0.05
4  Ice Cream Shop  0.03


----Marcanti----
                  venue  freq
0                   Bar  0.06
1        Ice Cream Shop  0.03
2              Bus Stop  0.03
3  Gym / Fitness Center  0.03
4           Coffee Shop  0.03


----Marine Etablissement----
                venue  freq
0          Restaurant  0.07
1                Café  0.07
2       Deli / Bodega  0.07
3         Flower Shop  0.04
4  Chinese Restaurant  0.04


----Marjoleinterrein----
           venue  freq
0       Bus Stop  0.18
1    Supermarket  0.18
2           Park  0.18
3     Restaurant  0.09
4  Shopping Mall  0.09


----Markengouw Midden----
            venue  freq
0        Bus Stop  0.22
1     Supermarket  0.22
2  Discount Store  0.11
3          Bakery  0.11
4   Grocery Store  0.11


----Markengouw Zuid----
            venue  freq
0        Bus Stop  0.22
1     Supermarket  0.22
2  Discount Store  0.11

               venue  freq
0                Bar  0.08
1              Hotel  0.07
2               Café  0.05
3  French Restaurant  0.04
4     Chocolate Shop  0.04


----Pieter van der Doesbuurt----
           venue  freq
0    Supermarket  0.04
1            Bar  0.04
2           Café  0.04
3    Pizza Place  0.04
4  Deli / Bodega  0.04


----Plan van Gool----
               venue  freq
0  Convenience Store  0.11
1        Supermarket  0.11
2  Electronics Store  0.07
3     Clothing Store  0.07
4     Sandwich Place  0.07


----Planciusbuurt Noord----
         venue  freq
0   Restaurant  0.10
1         Café  0.07
2  Pizza Place  0.05
3        Plaza  0.05
4       Bakery  0.05


----Planciusbuurt Zuid----
         venue  freq
0   Restaurant  0.10
1         Café  0.07
2  Pizza Place  0.05
3        Plaza  0.05
4       Bakery  0.05


----Postjeskade en omgeving----
               venue  freq
0               Café  0.12
1         Restaurant  0.12
2                Bar  0.09
3  French Restaurant  0.06

                    venue  freq
0             Supermarket  0.14
1           Shopping Mall  0.14
2  Furniture / Home Store  0.14
3                 Theater  0.14
4               Bookstore  0.14


----Twiske West----
                    venue  freq
0             Supermarket  0.14
1           Shopping Mall  0.14
2  Furniture / Home Store  0.14
3                 Theater  0.14
4               Bookstore  0.14


----Uilenburg----
             venue  freq
0      Coffee Shop  0.14
1              Bar  0.11
2           Hostel  0.08
3  Thai Restaurant  0.06
4            Hotel  0.06


----Utrechtsebuurt Zuid----
               venue  freq
0              Hotel  0.05
1        Coffee Shop  0.05
2  French Restaurant  0.05
3                Bar  0.05
4              Plaza  0.04


----Valeriusbuurt Oost----
                venue  freq
0               Hotel  0.09
1          Restaurant  0.07
2              Bakery  0.05
3   French Restaurant  0.05
4  Italian Restaurant  0.05


----Valeriusbuurt West----
      

In [25]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    return row_categories_sorted.index.values[0:num_top_venues]

In [26]:
import numpy as np
num_top_venues = 10
indicators = ['st', 'nd', 'rd']

columns = ['Naam']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Naam'] = amsterdam_grouped['Naam']

for ind in np.arange(amsterdam_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(amsterdam_grouped.iloc[ind, :], num_top_venues)
    
neighborhoods_venues_sorted.shape


(403, 11)

#### Clustering Neighborhoods

In this step we will cluster the neighbourhoods to visualize the comparable neighbourhoods. 
The clustering of the neighbourhoods will be done with the methode K means clustering. We selected 20 clusters

In [27]:
from sklearn.cluster import KMeans
import sklearn.cluster.k_means_
km = KMeans(n_clusters=3, init='k-means++', max_iter=100, n_init=1, 
  verbose=True)

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/sklearn/utils/deprecation.py:143: FutureWarning: The sklearn.cluster.k_means_ module is  deprecated in version 0.22 and will be removed in version 0.24. The corresponding classes / functions should instead be imported from sklearn.cluster. Anything that cannot be imported from sklearn.cluster is now part of the private API.
  warnings.warn(message, FutureWarning)


In [28]:
kclusters = 20
amsterdam_grouped_clustering = amsterdam_grouped.drop('Naam', 1)
kmeans = KMeans(n_clusters=kclusters, random_state=1).fit(amsterdam_grouped_clustering)
print(kmeans.labels_[0:20])
print(len(kmeans.labels_))

[13 13  9 14 15 15 15  4 13 15 15 18  7  7 18 16 16 16 16  4]
403


In [29]:
df.head()


Naam  Regio Postcode  Aantal inwoners   Latitude  \
0             Kop Zeedijk  Buurt     1012             1.10  52.373651   
1   Oude Kerk en omgeving  Buurt     1012           730.00  52.373651   
2         Burgwallen Oost  Buurt     1012             1.61  52.373651   
3         Nes en omgeving  Buurt     1012           350.00  52.373651   
4  Bg terrein en omgeving  Buurt     1012           670.00  52.373651   

   Longitude  
0   4.895564  
1   4.895564  
2   4.895564  
3   4.895564  
4   4.895564

In [30]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

amsterdam_merged = df
amsterdam_merged = amsterdam_merged.join(neighborhoods_venues_sorted.set_index('Naam'), on='Naam')

amsterdam_merged.head() # check the last columns!

Naam  Regio Postcode  Aantal inwoners   Latitude  \
0             Kop Zeedijk  Buurt     1012             1.10  52.373651   
1   Oude Kerk en omgeving  Buurt     1012           730.00  52.373651   
2         Burgwallen Oost  Buurt     1012             1.61  52.373651   
3         Nes en omgeving  Buurt     1012           350.00  52.373651   
4  Bg terrein en omgeving  Buurt     1012           670.00  52.373651   

   Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0   4.895564              15                 Hotel           Coffee Shop   
1   4.895564              15                 Hotel           Coffee Shop   
2   4.895564              15                 Hotel           Coffee Shop   
3   4.895564              15                 Hotel           Coffee Shop   
4   4.895564              15                 Hotel           Coffee Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                   Bar         Deli / Bodega                  Café   
1                   Bar         Deli / Bodega                  Café   
2                   Bar         Deli / Bodega                  Café   
3                   Bar         Deli / Bodega                  Café   
4                   Bar         Deli / Bodega                  Café   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0  Marijuana Dispensary        Chocolate Shop                Church   
1  Marijuana Dispensary        Chocolate Shop                Church   
2  Marijuana Dispensary        Chocolate Shop                Church   
3  Marijuana Dispensary        Chocolate Shop                Church   
4  Marijuana Dispensary        Chocolate Shop                Church   

  9th Most Common Venue 10th Most Common Venue  
0                   Pub      French Restaurant  
1                   Pub      French Restaurant  
2                   Pub      French Restaurant  
3                   Pub      French Restaurant  
4                   Pub      French Restaurant

#### Finally visualization of the resulting cluster

In [31]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

markers_colors = []
for lat, lon, poi, cluster in zip(amsterdam_merged['Latitude'], amsterdam_merged['Longitude'], amsterdam_merged['Naam'], amsterdam_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + 'Cluster' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon], 
        radius=5, 
        popup=label, 
        color=rainbow[cluster-1], 
        fill=True, 
        fill_color=rainbow[cluster-1], 
        fill_opacity=0.7).add_to(map_clusters)
map_clusters

# 2. How many competing Italian restaurants has each neighbourhood?

We start by selecting the Italian restaurants from the Foursquare API

In [32]:
italian = amsterdam_venues[amsterdam_venues['Venue Category'] == 'Italian Restaurant']
italian

Neighborhood  Neighborhood Latitude  \
62                                Kop Zeedijk              52.373651   
132                     Oude Kerk en omgeving              52.373651   
202                           Burgwallen Oost              52.373651   
272                           Nes en omgeving              52.373651   
342                    Bg terrein en omgeving              52.373651   
412                                 Hemelrijk              52.373651   
482                         Nieuwendijk Noord              52.373651   
552                          Spuistraat Noord              52.373651   
622                   Nieuwe Kerk en omgeving              52.373651   
692                           Spuistraat Zuid              52.373651   
762                            Begijnhofbuurt              52.373651   
832                            Kalverdriehoek              52.373651   
850                   Langestraat en omgeving              52.378873   
854                   Langestraat en omgeving              52.378873   
872                   Langestraat en omgeving              52.378873   
912                   Langestraat en omgeving              52.378873   
918                   Langestraat en omgeving              52.378873   
935                   Langestraat en omgeving              52.378873   
937                   Langestraat en omgeving              52.378873   
949                   Leliegracht en omgeving              52.370495   
988                   Leliegracht en omgeving              52.370495   
997                   Leliegracht en omgeving              52.370495   
1020                  Leliegracht en omgeving              52.370495   
1049                       Felix Meritisbuurt              52.370495   
1088                       Felix Meritisbuurt              52.370495   
1097                       Felix Meritisbuurt              52.370495   
1120                       Felix Meritisbuurt              52.370495   
1149                       Leidsegracht Noord              52.370495   
1188                       Leidsegracht Noord              52.370495   
1197                       Leidsegracht Noord              52.370495   
1220                       Leidsegracht Noord              52.370495   
1263                             Spiegelbuurt              52.363149   
1344                             Gouden Bocht              52.363149   
1425                            Van Loonbuurt              52.363149   
1506                          Amstelveldbuurt              52.363149   
1587                      Rembrandtpleinbuurt              52.363149   
1668                           Reguliersbuurt              52.363149   
1749                        Leidsegracht Zuid              52.363149   
2177                         Westerdokseiland              52.388312   
2236                     Haarlemmerbuurt Oost              52.388312   
2295                     Haarlemmerbuurt West              52.388312   
2354                      Westelijke Eilanden              52.388312   
2413                      Planciusbuurt Noord              52.388312   
2472                       Planciusbuurt Zuid              52.388312   
2495                            Driehoekbuurt              52.378873   
2499                            Driehoekbuurt              52.378873   
2517                            Driehoekbuurt              52.378873   
2557                            Driehoekbuurt              52.378873   
2563                            Driehoekbuurt              52.378873   
2580                            Driehoekbuurt              52.378873   
2582                            Driehoekbuurt              52.378873   
2594                         Bloemgrachtbuurt              52.370495   
2633                         Bloemgrachtbuurt              52.370495   
2642                         Bloemgrachtbuurt              52.370495   
2665                         Bloemgrachtbuurt              52.370495   
2

In [33]:
italian.shape

(409, 7)

#### Make a map of the Italian restaurants 

In [34]:
# create map of Amsterdam using latitude and longitude values
map_amsterdam2 = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, lng, naam, neighborhood in zip(italian['Venue Latitude'], italian['Venue Longitude'], italian['Venue'], italian['Neighborhood']):
    #label = '{}. {} 'format(naam)
    label = folium.Popup(str(naam) + ' in ' + str(neighborhood), parse_html=True)
    #label = '{}'.format(naam, neighborhood)
    #label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_amsterdam2)
map_amsterdam2

Now we have to select the relevant neighbourhoods. This means that we have to select only those neighbourhoods that have a possible location for our new Italian restaurant

#### The list of de possible locations for the new restaurant

In [47]:
# Here we add the list of the possible locactions as provided by the real estate agent. 
d = {'id':["1", "2", "3", "4","5", "6", "7", "8", "9", "10"], 
    'Adress': ["Leidseplein 9", "Delflandplein 22", "Meer en Vaart 405", "Leidsekruisstraat 11", "Oostelijke Handelskade 4", "Osdorpplein 1014", "Reguliersgracht 110", "Jacob Bontiusplaats 10", "Roetersstraat 15", "Arnold Schönberglaan 9"
], 
    'Postalcode':["1017 PS", "1062 HR", "1068 LH", "1017 RE", "1019 HM", "1068 TG", "1017 LX", "1018 LL", "1018 WD", "1082 MJ"]}

dataframe  = pd.DataFrame(d)

In [48]:
# Check whether the list has been proceeded correctly
dataframe

id                    Adress Postalcode
0   1             Leidseplein 9    1017 PS
1   2          Delflandplein 22    1062 HR
2   3         Meer en Vaart 405    1068 LH
3   4      Leidsekruisstraat 11    1017 RE
4   5  Oostelijke Handelskade 4    1019 HM
5   6          Osdorpplein 1014    1068 TG
6   7       Reguliersgracht 110    1017 LX
7   8    Jacob Bontiusplaats 10    1018 LL
8   9          Roetersstraat 15    1018 WD
9  10    Arnold Schönberglaan 9    1082 MJ

In [51]:
# Add information on the postal codes and latititude and longitude 
postal_codes = dataframe['Postalcode']    
coords = [ get_latilong(postal_code) for postal_code in postal_codes.tolist() ]

In [52]:
# Adding Columns Latitude & Longitude
df_coords2 = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])
dataframe['Latitude'] = df_coords2['Latitude']
dataframe['Longitude'] = df_coords2['Longitude']

In [53]:
# Check whether the information has been added correctly
dataframe

id                    Adress Postalcode   Latitude  Longitude
0   1             Leidseplein 9    1017 PS  52.363584   4.882521
1   2          Delflandplein 22    1062 HR  52.349824   4.840188
2   3         Meer en Vaart 405    1068 LH  52.354856   4.809594
3   4      Leidsekruisstraat 11    1017 RE  52.363532   4.885120
4   5  Oostelijke Handelskade 4    1019 HM  52.375823   4.927369
5   6          Osdorpplein 1014    1068 TG  52.357788   4.805442
6   7       Reguliersgracht 110    1017 LX  52.360530   4.895871
7   8    Jacob Bontiusplaats 10    1018 LL  52.371487   4.927335
8   9          Roetersstraat 15    1018 WD  52.363349   4.910447
9  10    Arnold Schönberglaan 9    1082 MJ  52.337811   4.870943

#### Visualize the selected locations

In [54]:
# create map of Amsterdam using latitude and longitude values
map_amsterdam3 = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, lng, adres in zip(dataframe['Latitude'], dataframe['Longitude'], dataframe['Adress']):
    label = folium.Popup(str(adres), parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='red',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_amsterdam3)
map_amsterdam3

The separate maps look good, it seems more useful when we combine the information on the maps.

### combine the list of possible locations with the competing Italian restaurants 

In [55]:
# add clustering labels

amsterdam_merged.head() 

italiancompetitors = df
italiancompetitors = amsterdam_merged.join(neighborhoods_venues_sorted.set_index('Naam'), on='Naam')


ValueError: columns overlap but no suffix specified: Index(['Cluster Labels', '1st Most Common Venue', '2nd Most Common Venue',
       '3rd Most Common Venue', '4th Most Common Venue',
       '5th Most Common Venue', '6th Most Common Venue',
       '7th Most Common Venue', '8th Most Common Venue',
       '9th Most Common Venue', '10th Most Common Venue'],
      dtype='object')

In [56]:
# create map of Amsterdam using latitude and longitude values
map_amsterdam4 = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, lng, adres in zip(dataframe['Latitude'], dataframe['Longitude'], dataframe['Adress']):
    label = folium.Popup(str(adres), parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='red',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_amsterdam4)

for lat, lng, naam, neighborhood in zip(italian['Venue Latitude'], italian['Venue Longitude'], italian['Venue'], italian['Neighborhood']):
    #label = '{}. {} 'format(naam)
    label = folium.Popup(str(naam) + ' in ' + str(neighborhood), parse_html=True)
    #label = '{}'.format(naam, neighborhood)
    #label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_amsterdam4)

    
map_amsterdam4

### Draw a map of the cluster of the nieghbourhoods and the possible locations

In [58]:
map_clusters2 = folium.Map(location=[latitude, longitude], zoom_start=11)

x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

markers_colors = []
for lat, lon, poi, cluster in zip(amsterdam_merged['Latitude'], amsterdam_merged['Longitude'], amsterdam_merged['Naam'], amsterdam_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + 'Cluster' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon], 
        radius=4, 
        popup=label, 
        color=rainbow[cluster-1], 
        fill=True, 
        fill_color=rainbow[cluster-1], 
        fill_opacity=0.7).add_to(map_clusters2)


for lat, lng, adres in zip(dataframe['Latitude'], dataframe['Longitude'], dataframe['Adress']):
    label = folium.Popup(str(adres), parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='red',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_clusters2)
        
map_clusters2

Our restaurants are located in 5 clusters: 0, 18, 4, 15 and 9. So let's have a closer look at these clusters. 

#### Examine the clusters that have the possible locations for the new restaurant

In [59]:
# Check the clusters near the possible locations of our restaurant
# Cluster 0 Osdorp Zuidoost for the Meer en Vaart Location and the Osdorpplein Location
amsterdam_merged.loc[amsterdam_merged['Cluster Labels'] == 0, amsterdam_merged.columns[[1] + list(range(5, amsterdam_merged.shape[1]))]]

Regio  Longitude  Cluster Labels      1st Most Common Venue  \
247  Buurt   4.935428               0          Convenience Store   
250  Buurt   4.935428               0          Convenience Store   
252  Buurt   4.935428               0          Convenience Store   
253  Buurt   4.935428               0          Convenience Store   
259  Buurt   4.890133               0                  Bookstore   
260  Buurt   4.890133               0                  Bookstore   
261  Buurt   4.890133               0                  Bookstore   
263  Buurt   4.890133               0                  Bookstore   
266  Buurt   4.890133               0                  Bookstore   
273  Buurt   4.935428               0          Convenience Store   
274  Buurt   4.935428               0          Convenience Store   
275  Buurt   4.935428               0          Convenience Store   
276  Buurt   4.935428               0          Convenience Store   
277  Buurt   4.935428               0          Convenience Store   
278  Buurt   4.935428               0          Convenience Store   
295  Buurt   4.935428               0          Convenience Store   
296  Buurt   4.935428               0          Convenience Store   
297  Buurt   4.935428               0          Convenience Store   
318  Buurt   4.806918               0              Shopping Mall   
319  Buurt   4.806918               0              Shopping Mall   
320  Buurt   4.806918               0              Shopping Mall   
321  Buurt   4.806918               0              Shopping Mall   
322  Buurt   4.806918               0              Shopping Mall   
323  Buurt   4.788174               0               Tram Station   
324  Buurt   4.788174               0               Tram Station   
325  Buurt   4.788174               0               Tram Station   
326  Buurt   4.788174               0               Tram Station   
327  Buurt   4.788174               0               Tram Station   
328  Buurt   4.788174               0               Tram Station   
376  Buurt   4.974811               0  Middle Eastern Restaurant   
377  Buurt   4.974811               0  Middle Eastern Restaurant   
378  Buurt   4.974811               0  Middle Eastern Restaurant   
379  Buurt   4.979827               0                Supermarket   
380  Buurt   4.979827               0                Supermarket   
381  Buurt   4.979827               0                Supermarket   
382  Buurt   4.979827               0                Supermarket   
383  Buurt   4.979827               0                Supermarket   
384  Buurt   4.974811               0  Middle Eastern Restaurant   
385  Buurt   4.974811               0  Middle Eastern Restaurant   
386  Buurt   4.974811               0  Middle Eastern Restaurant   
387  Buurt   4.974811               0  Middle Eastern Restaurant   
388  Buurt   4.979827               0                Supermarket   
394  Buurt   4.980839               0                IT Services   
395  Buurt   4.980839               0                IT Services   
396  Buurt   4.980839               0                IT Services   
398  Buurt   4.980839               0                IT Services   
400  Buurt   4.980839               0                IT Services   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
247           Supermarket     Electronics Store        Clothing Store   
250           Supermarket     Electronics Store        Clothing Store   
252           Supermarket     Electronics Store        Clothing Store   
253           Supermarket     Electronics Store        Clothing Store   
259           Supermarket               Theater         Shopping Mall   
260           Supermarket               Theater         Shopping Mall   
261           Supermarket               Theater         Shopping Mall   
263           Supermarket               Theater         Shopping Mall   
266           Supermarket               Theater         Shopping Mall   
273       

In [60]:
# Cluster 18 for Location Delflandplein and Architectenbuurt
amsterdam_merged.loc[amsterdam_merged['Cluster Labels'] == 18, amsterdam_merged.columns[[1] + list(range(5, amsterdam_merged.shape[1]))]]

Regio  Longitude  Cluster Labels 1st Most Common Venue  \
61   Buurt   4.933626              18            Restaurant   
135  Buurt   4.933626              18            Restaurant   
136  Buurt   4.933626              18            Restaurant   
137  Buurt   4.933626              18            Restaurant   
138  Buurt   4.933626              18            Restaurant   
139  Buurt   4.933626              18            Restaurant   
140  Buurt   4.933626              18            Restaurant   
141  Buurt   4.933626              18            Restaurant   
142  Buurt   4.933626              18            Restaurant   
147  Buurt   4.982629              18         Design Studio   
148  Buurt   4.982629              18         Design Studio   
155  Buurt   4.853991              18           Coffee Shop   
156  Buurt   4.853991              18           Coffee Shop   
159  Buurt   4.853991              18           Coffee Shop   
160  Buurt   4.853991              18           Coffee Shop   
161  Buurt   4.853991              18           Coffee Shop   
165  Buurt   4.853991              18           Coffee Shop   
166  Buurt   4.853991              18           Coffee Shop   
167  Buurt   4.853991              18           Coffee Shop   
168  Buurt   4.853991              18           Coffee Shop   
169  Buurt   4.853991              18           Coffee Shop   
170  Buurt   4.853991              18           Coffee Shop   
171  Buurt   4.853832              18            Restaurant   
172  Buurt   4.853832              18            Restaurant   
173  Buurt   4.853832              18            Restaurant   
174  Buurt   4.853832              18            Restaurant   
262  Buurt   4.860529              18                   Gym   
298  Buurt   4.853832              18            Restaurant   
299  Buurt   4.853832              18            Restaurant   
300  Buurt   4.853832              18            Restaurant   
301  Buurt   4.853832              18            Restaurant   
304  Buurt   4.821514              18                  Park   
305  Buurt   4.821514              18                  Park   
307  Buurt   4.821514              18                  Park   
309  Buurt   4.821514              18                  Park   
329  Buurt   4.779147              18          Tram Station   
330  Buurt   4.779147              18          Tram Station   
331  Buurt   4.821514              18                  Park   
333  Buurt   4.837992              18           Supermarket   
335  Buurt   4.837992              18           Supermarket   
336  Buurt   4.853832              18            Restaurant   
338  Buurt   4.837992              18           Supermarket   
340  Buurt   4.837992              18           Supermarket   
343  Buurt   4.837992              18           Supermarket   
344  Buurt   4.837992              18           Supermarket   
345  Buurt   4.837992              18           Supermarket   
355  Buurt   4.837992              18           Supermarket   

    2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
61                   Café         Deli / Bodega      Chinese Restaurant   
135                  Café         Deli / Bodega      Chinese Restaurant   
136                  Café         Deli / Bodega      Chinese Restaurant   
137                  Café         Deli / Bodega      Chinese Restaurant   
138                  Café         Deli / Bodega      Chinese Restaurant   
139                  Café         Deli / Bodega      Chinese Restaurant   
140                  Café         Deli / Bodega      Chinese Restaurant   
141                  Café         Deli / Bodega      Chinese Restaurant   
142                  Café         Deli / Bodega      Chinese Restaurant   
147       Harbor / Marina           Flower Shop  Furniture / Home Store   
148       Harbor / Marina           Flower Shop  Furniture / Home Store   
155         Deli / Bodega                   Bar             Supermarket   
156  

In [61]:
# Cluster 4 for Arnold Schonberglaan
amsterdam_merged.loc[amsterdam_merged['Cluster Labels'] == 4, amsterdam_merged.columns[[1] + list(range(5, amsterdam_merged.shape[1]))]]

Regio  Longitude  Cluster Labels 1st Most Common Venue  \
77   Buurt   4.873620               4           Coffee Shop   
78   Buurt   4.873620               4           Coffee Shop   
79   Buurt   4.870223               4                   Bar   
80   Buurt   4.870223               4                   Bar   
81   Buurt   4.870223               4                   Bar   
82   Buurt   4.870223               4                   Bar   
83   Buurt   4.870223               4                   Bar   
84   Buurt   4.870223               4                   Bar   
86   Buurt   4.873620               4           Coffee Shop   
87   Buurt   4.873620               4           Coffee Shop   
88   Buurt   4.867659               4                  Café   
89   Buurt   4.867659               4                  Café   
90   Buurt   4.867659               4                  Café   
91   Buurt   4.867659               4                  Café   
92   Buurt   4.867659               4                  Café   
93   Buurt   4.867659               4                  Café   
94   Buurt   4.868186               4                  Café   
95   Buurt   4.868186               4                  Café   
96   Buurt   4.868186               4                  Café   
97   Buurt   4.868186               4                  Café   
99   Buurt   4.875433               4                 Hotel   
100  Buurt   4.875433               4                 Hotel   
101  Buurt   4.857654               4            Restaurant   
103  Buurt   4.875326               4      Sushi Restaurant   
104  Buurt   4.875326               4      Sushi Restaurant   
105  Buurt   4.904705               4    Italian Restaurant   
106  Buurt   4.892937               4        Breakfast Spot   
107  Buurt   4.892937               4        Breakfast Spot   
108  Buurt   4.892937               4        Breakfast Spot   
109  Buurt   4.892937               4        Breakfast Spot   
110  Buurt   4.904705               4    Italian Restaurant   
111  Buurt   4.898256               4    Italian Restaurant   
112  Buurt   4.892937               4        Breakfast Spot   
113  Buurt   4.892937               4        Breakfast Spot   
114  Buurt   4.904705               4    Italian Restaurant   
115  Buurt   4.898256               4    Italian Restaurant   
116  Buurt   4.898256               4    Italian Restaurant   
117  Buurt   4.913601               4    Italian Restaurant   
118  Buurt   4.913601               4    Italian Restaurant   
119  Buurt   4.913601               4    Italian Restaurant   
120  Buurt   4.913601               4    Italian Restaurant   
121  Buurt   4.921790               4           Coffee Shop   
122  Buurt   4.921790               4           Coffee Shop   
123  Buurt   4.913601               4    Italian Restaurant   
124  Buurt   4.921790               4           Coffee Shop   
125  Buurt   4.929690               4                Market   
126  Buurt   4.929690               4                Market   
127  Buurt   4.913601               4    Italian Restaurant   
128  Buurt   4.921790               4           Coffee Shop   
129  Buurt   4.935917               4           Coffee Shop   
130  Buurt   4.935917               4           Coffee Shop   
131  Buurt   4.935917               4           Coffee Shop   
153  Buurt   4.851446               4                Bakery   
154  Buurt   4.851446               4                Bakery   
157  Buurt   4.851446               4                Bakery   
158  Buurt   4.851446               4                Bakery   
184  Buurt   4.875433               4                 Hotel   
187  Buurt   4.875433               4                 Hotel   
188  Buurt   4.875433               4                 Hotel   
189  Buurt   4.875433               4                 Hotel   
190  Buurt   4.875433               4                 Hotel   
191  Buurt   4.875433               4                 Hotel   
192  Buurt   4.875433               

In [62]:
# CLuster 15
amsterdam_merged.loc[amsterdam_merged['Cluster Labels'] == 15, amsterdam_merged.columns[[1] + list(range(5, amsterdam_merged.shape[1]))]]

Regio  Longitude  Cluster Labels 1st Most Common Venue  \
0    Buurt   4.895564              15                 Hotel   
1    Buurt   4.895564              15                 Hotel   
2    Buurt   4.895564              15                 Hotel   
3    Buurt   4.895564              15                 Hotel   
4    Buurt   4.895564              15                 Hotel   
5    Buurt   4.895564              15                 Hotel   
6    Buurt   4.895564              15                 Hotel   
7    Buurt   4.895564              15                 Hotel   
8    Buurt   4.895564              15                 Hotel   
9    Buurt   4.895564              15                 Hotel   
10   Buurt   4.895564              15                 Hotel   
11   Buurt   4.895564              15                 Hotel   
12   Buurt   4.884873              15                   Bar   
13   Buurt   4.882398              15                   Bar   
14   Buurt   4.882398              15                   Bar   
15   Buurt   4.882398              15                   Bar   
16   Buurt   4.891889              15           Coffee Shop   
17   Buurt   4.891889              15           Coffee Shop   
18   Buurt   4.891889              15           Coffee Shop   
19   Buurt   4.891889              15           Coffee Shop   
20   Buurt   4.891889              15           Coffee Shop   
21   Buurt   4.891889              15           Coffee Shop   
22   Buurt   4.891889              15           Coffee Shop   
23   Buurt   4.904718              15           Coffee Shop   
24   Buurt   4.904718              15           Coffee Shop   
25   Buurt   4.904718              15           Coffee Shop   
26   Buurt   4.904718              15           Coffee Shop   
27   Buurt   4.904718              15           Coffee Shop   
28   Buurt   4.904718              15           Coffee Shop   
29   Buurt   4.904718              15           Coffee Shop   
30   Buurt   4.904718              15           Coffee Shop   
31   Buurt   4.904718              15           Coffee Shop   
38   Buurt   4.884873              15                   Bar   
39   Buurt   4.882398              15                   Bar   
40   Buurt   4.884873              15                   Bar   
41   Buurt   4.884873              15                   Bar   
42   Buurt   4.882398              15                   Bar   
43   Buurt   4.882398              15                   Bar   
44   Buurt   4.882398              15                   Bar   
45   Buurt   4.882398              15                   Bar   
46   Buurt   4.882398              15                   Bar   
47   Buurt   4.884873              15                   Bar   
48   Buurt   4.884873              15                   Bar   
49   Buurt   4.891889              15           Coffee Shop   
50   Buurt   4.891889              15           Coffee Shop   
51   Buurt   4.891889              15           Coffee Shop   
52   Buurt   4.891889              15           Coffee Shop   
53   Buurt   4.891889              15           Coffee Shop   
54   Buurt   4.891889              15           Coffee Shop   
55   Buurt   4.891889              15           Coffee Shop   
56   Buurt   4.891889              15           Coffee Shop   
57   Buurt   4.904718              15           Coffee Shop   
68   Buurt   4.904718              15           Coffee Shop   
69   Buurt   4.867152              15           Pizza Place   
85   Buurt   4.884873              15                   Bar   
152  Buurt   4.867152              15           Pizza Place   
237  Buurt   4.916960              15                 Hotel   
238  Buurt   4.916960              15                 Hotel   
239  Buurt   4.916960              15                 Hotel   
240  Buurt   4.916960              15                 Hotel   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0             Coffee Shop                   Bar         Deli / Bodega   
1             C

In [65]:
# CLuster 9
amsterdam_merged.loc[amsterdam_merged['Cluster Labels'] == 9, amsterdam_merged.columns[[1] + list(range(5, amsterdam_merged.shape[1]))]]

Regio  Longitude  Cluster Labels 1st Most Common Venue  \
58  Buurt   4.917282               9           Zoo Exhibit   
59  Buurt   4.917282               9           Zoo Exhibit   
60  Buurt   4.917282               9           Zoo Exhibit   
62  Buurt   4.917282               9           Zoo Exhibit   
63  Buurt   4.917282               9           Zoo Exhibit   
64  Buurt   4.917282               9           Zoo Exhibit   
65  Buurt   4.917282               9           Zoo Exhibit   
66  Buurt   4.917282               9           Zoo Exhibit   
67  Buurt   4.917282               9           Zoo Exhibit   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
58                  Café                   Bar        History Museum   
59                  Café                   Bar        History Museum   
60                  Café                   Bar        History Museum   
62                  Café                   Bar        History Museum   
63                  Café                   Bar        History Museum   
64                  Café                   Bar        History Museum   
65                  Café                   Bar        History Museum   
66                  Café                   Bar        History Museum   
67                  Café                   Bar        History Museum   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
58           Pizza Place                 Plaza           Coffee Shop   
59           Pizza Place                 Plaza           Coffee Shop   
60           Pizza Place                 Plaza           Coffee Shop   
62           Pizza Place                 Plaza           Coffee Shop   
63           Pizza Place                 Plaza           Coffee Shop   
64           Pizza Place                 Plaza           Coffee Shop   
65           Pizza Place                 Plaza           Coffee Shop   
66           Pizza Place                 Plaza           Coffee Shop   
67           Pizza Place                 Plaza           Coffee Shop   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
58            Restaurant        Breakfast Spot            Supermarket  
59            Restaurant        Breakfast Spot            Supermarket  
60            Restaurant        Breakfast Spot            Supermarket  
62            Restaurant        Breakfast Spot            Supermarket  
63            Restaurant        Breakfast Spot            Supermarket  
64            Restaurant        Breakfast Spot            Supermarket  
65            Restaurant        Breakfast Spot            Supermarket  
66            Restaurant        Breakfast Spot            Supermarket  
67            Restaurant        Breakfast Spot            Supermarket

#### Reduced list of possible locations and competitions

In [66]:
# Lets now use the information of the clusters to take another look at the Italian restaurants. 
# The restaurants in cluster 15 and 0 did not seem suitable for the restaurant. So lets have another look at the information on the competing restaurants. 
# We drop the restaurants with the not recommended neighbourhoods. 

dataframe2 = dataframe.drop([0,2,3,5,6])
dataframe2

id                    Adress Postalcode   Latitude  Longitude
1   2          Delflandplein 22    1062 HR  52.349824   4.840188
4   5  Oostelijke Handelskade 4    1019 HM  52.375823   4.927369
7   8    Jacob Bontiusplaats 10    1018 LL  52.371487   4.927335
8   9          Roetersstraat 15    1018 WD  52.363349   4.910447
9  10    Arnold Schönberglaan 9    1082 MJ  52.337811   4.870943

In [67]:
# Draw a map of these possible locations and the competition
# create map of Amsterdam using latitude and longitude values
map_amsterdam5 = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, lng, adres in zip(dataframe2['Latitude'], dataframe2['Longitude'], dataframe2['Adress']):
    label = folium.Popup(str(adres), parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='red',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_amsterdam5)

for lat, lng, naam, neighborhood in zip(italian['Venue Latitude'], italian['Venue Longitude'], italian['Venue'], italian['Neighborhood']):
    #label = '{}. {} 'format(naam)
    label = folium.Popup(str(naam) + ' in ' + str(neighborhood), parse_html=True)
    #label = '{}'.format(naam, neighborhood)
    #label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_amsterdam5)

    
map_amsterdam5